In [250]:
from config import sparqlTerms, mig_ns, sparql_mig_test, sparql_mig_simple, sparql_mig_dev, vocabs
from transformation import TransformationFactory
from SPARQLWrapper import JSON
from utilities import removeNS, PrintException
import concurrent.futures
import re

##  MAIN CONTROLLER

In [251]:
def main():
	for ptype in ["collection", "community", "generic", "thesis"]:
		mig = QueryFactory.getMigrationQuery(ptype)
		for q in mig.queries:
			DTO = DataFactory.getData(q, mig)
			DTO.transformData()

##  TRANSFORMATIONS
#### functions for handling data passed over by the data object. Takes a triple, detects what kind of action needs to be taken based on the predicate, sends it to the appropriate function for transformations, then returns it back to the data handler to be saved.

In [252]:
class Transformation():
    """
    the output must be a list of triples matching the same format as the input (as follows):
    {
        'subject': {
            'value': 'http://gillingham.library.ualberta.ca:8080/fedora/rest/prod/0r/96/76/28/0r967628d', 
            'type': 'uri'
        }, 
        'predicate': {
            'value': 'http://purl.org/dc/elements/1.1/subject', 
            'type': 'uri'
        }, 
        'object': {
            'value': 'Geochemistry', 
            'type': 'literal'}
        }
    }
    """
    def __init__(self):
        self.output = []

    def rdfsyntaxnstype(self, triple, ptype):
        # nothing yet
        self.output.append(triple)
        return self.output # a list of triples, in case more triples must be added as a result of this operation     
    









#### transformation on dcterms:language

#### transformation on dcterms:language

In [ ]:
    def language(self, triple, ptype):
        # normalize values and convert to URI (consult the "vocabs" variable from the config file (this folder))
        self.output.append(triple)
        return self.output

#### transformation on dc:rights

In [ ]:
    def rights(self, triple, ptype):
        # several different license values need to be coerced into one common value, this needs to be confirmed with leah before it is written
        self.output.append(triple)
        return self.output

#### transformation on ual:institution

In [ ]:
    def institution(self, triple, ptype):
        # convert university of alberta to <http://id.loc.gov/authorities/names/n79058482>
        self.output.append(triple)
        return self.output

#### transformation on dcterms:license

In [ ]:
    def license(self, triple, ptype):
        # convert licenses from text to URI (use vocabs variable, some coersion will be necessary)
        self.output.append(triple)
        return self.output 

#### transformation on dcterms:type

In [ ]:
    def type(self, triple, ptype):
        if ptype == 'thesis':
            # should be no dctype for thesis, bibo type should already exist
            pass
        elif ptype == 'generic':
            # unaccounted for types:
                # null
                # Complete
                # processing
            for vocab in vocabs["type"]:
                # mint a new triple with the mapped type
                if triple['object']['value'] in vocab["mapping"]:
                    self.output.append(
                        {
                            'subject': {
                                'value': triple['subject']['value'], # the subject of the triple
                                'type': 'uri'
                            }, 
                            'predicate': {
                                'value': triple['predicate']['value'], # the predicate of the triple
                                'type': 'uri'
                            }, 
                            'object': {
                                'value': vocab["uri"], # mapped uri
                                'type': 'uri'}
                            }
                        }
                    )
                if "Draft-Submitted" in triple['object']['value']:
                    self.output.append( 
                        {
                            'subject': {
                                'value': triple['subject']['value'], # the subject of the triple
                                'type': 'uri'
                            }, 
                            'predicate': {
                                'value': "http://purl.org/ontology/bibo/status", # the predicate of the triple
                                'type': 'uri'
                            }, 
                            'object': {
                                'value': "http://vivoweb.org/ontology/core#submitted", # mapped uri
                                'type': 'uri'}
                            }
                        },
                         {
                            'subject': {
                                'value': triple['subject']['value'], # the subject of the triple
                                'type': 'uri'
                            }, 
                            'predicate': {
                                'value': "http://purl.org/ontology/bibo/status", # the predicate of the triple
                                'type': 'uri'
                            }, 
                            'object': {
                                'value': "http://purl.org/ontology/bibo/status#draft", # mapped uri
                                'type': 'uri'}
                            }
                        }
                    )
                if "Published" in triple['object']['value']:
                    self.output.append( 
                        {
                         {
                            'subject': {
                                'value': triple['subject']['value'], # the subject of the triple
                                'type': 'uri'
                            }, 
                            'predicate': {
                                'value': "http://purl.org/ontology/bibo/status", # the predicate of the triple
                                'type': 'uri'
                            }, 
                            'object': {
                                'value': "http://purl.org/ontology/bibo/status#published", # mapped uri
                                'type': 'uri'}
                            }
                        }
                    )
        elif (ptype == 'community') or (ptype == 'collection'):
            self.output.append(triple)
   # <>
   # <http://purl.org/ontology/bibo/status#draft)>
        
        return self.output

##  QUERY BUILDER
##### Pulls current mappings from triplestore, dynamically builds queries in managable sizes

In [253]:
class Query(object):
    """ Query objects are dynamically generated, and contain SPARQL CONSTRUCT queries with input from the jupiter application profile """
    def __init__(self, ptype, sparqlTerms=sparqlTerms, sparqlData=sparql_mig_test):
        self.mapping = []
        self.sparqlTerms = sparqlTerms  # doesn't need to change (the terms store doesn't change)
        self.sparqlData = sparqlData  # sets the triple store from which to get data (simple, test, or dev)
        self.queries = []
        self.prefixes = ""
        self.filename = ""
        for ns in mig_ns:
            self.prefixes = self.prefixes + " PREFIX %s: <%s> " % (ns['prefix'], ns['uri'])
        self.getMappings()
        self.generateQueries()

    def getMappings(self):
        query = "prefix ual: <http://terms.library.ualberta.ca/>SELECT * WHERE {GRAPH ual:%s {?newProperty ual:backwardCompatibleWith ?oldProperty} }" % (self.ptype)
        self.sparqlTerms.setReturnFormat(JSON)
        self.sparqlTerms.setQuery(query)
        results = self.sparqlTerms.query().convert()
        for result in results['results']['bindings']:
            self.mapping.append((result['newProperty']['value'], result['oldProperty']['value']))

    def generateQueries(self):
        pass


class Collection(Query):
    def __init__(self):
        self.ptype = 'collection'
        self.construct = "CONSTRUCT { ?resource info:hasModel 'IRItem'^^xsd:string ; rdf:type pcdm:Collection"
        self.where = ["WHERE { ?resource info:hasModel 'Collection'^^xsd:string . OPTIONAL { ?resource ualids:is_community 'false'^^xsd:boolean } . OPTIONAL { ?resource ualid:is_community 'false'^^xsd:boolean } . OPTIONAL { ?resource ual:is_community 'false'^^xsd:boolean }"]
        self.select = None
        super().__init__(self.ptype)

    def generateQueries(self):
        for where in self.where:
            construct = self.construct
            for pair in self.mapping:
                construct = "%s ; <%s> ?%s" % (construct, pair[0], removeNS(pair[0]))
                where = " %s . OPTIONAL { ?resource <%s> ?%s }" % (where, pair[1], removeNS(pair[0]))
            self.queries.append( ("%s %s } %s }" % (self.prefixes, construct, where), "" ) )


class Community(Query):
    def __init__(self):
        self.ptype = 'community'
        self.construct = "CONSTRUCT { ?resource info:hasModel 'IRItem'^^xsd:string ; rdf:type pcdm:Object; rdf:type ual:Community"
        self.where = ["WHERE { ?resource info:hasModel 'Collection'^^xsd:string ; OPTIONAL { ?resource ualids:is_community 'true'^^xsd:boolean } . OPTIONAL { ?resource ualid:is_community 'true'^^xsd:boolean } . OPTIONAL { ?resource ual:is_community 'true'^^xsd:boolean }"]
        self.select = None
        super().__init__(self.ptype)

    def generateQueries(self):
        for where in self.where:
            construct = self.construct
            for pair in self.mapping:
                construct = "%s ; <%s> ?%s" % (construct, pair[0], removeNS(pair[0]))
                where = " %s . OPTIONAL { ?resource <%s> ?%s }" % (where, pair[1], removeNS(pair[0]))
            self.queries.append( ( "%s %s } %s }" % (self.prefixes, construct, where), "" ) )


class Generic(Query):
    def __init__(self):
        self.ptype = 'generic'
        self.construct = "CONSTRUCT { ?resource info:hasModel 'IRItem'^^xsd:string ; rdf:type pcdm:Object; rdf:type works:work"
        self.where = []
        self.select = "SELECT distinct ?collection WHERE { ?resource info:hasModel 'GenericFile'^^xsd:string ; dcterm:type ?type . filter(?type != 'Thesis'^^xsd:string) . ?resource ualids:hasCollectionId ?collection }"
        super().__init__(self.ptype)

    def generateQueries(self):
        query = "%s %s" % (self.prefixes, self.select)
        self.sparqlData.setReturnFormat(JSON)
        self.sparqlData.setQuery(query)
        results = self.sparqlData.query().convert()
        for result in results['results']['bindings']:
            where = "WHERE {  ?resource ualids:hasCollectionId '%s'^^xsd:string ; info:hasModel 'GenericFile'^^xsd:string ; dcterm:type ?type . filter(?type != 'Thesis'^^xsd:string)" % (result['collection']['value'])
            construct = self.construct
            for pair in self.mapping:
                construct = "%s ; <%s> ?%s" % (construct, pair[0], removeNS(pair[0]))
                where = " %s . OPTIONAL { ?resource <%s> ?%s }" % (where, pair[1], removeNS(pair[0]))
            self.queries.append( ( "%s %s } %s }" % (self.prefixes, construct, where), result['collection']['value'] ) )

class Thesis(Query):
    def __init__(self):
        self.ptype = 'thesis'
        self.construct = "CONSTRUCT { ?resource info:hasModel 'IRItem'^^xsd:string ; rdf:type pcdm:Object; rdf:type works:work ; rdf:type bibo:Thesis"
        self.where = []
        self.select = "SELECT distinct ?year_created WHERE { ?resource info:hasModel 'GenericFile'^^xsd:string ; dcterm:type 'Thesis'^^xsd:string ; ualids:year_created ?year_created }"
        super().__init__(self.ptype)

    def generateQueries(self):
        query = "%s %s" % (self.prefixes, self.select)
        self.sparqlData.setReturnFormat(JSON)
        self.sparqlData.setQuery(query)
        results = self.sparqlData.query().convert()
        for result in results['results']['bindings']:
            where = "WHERE { ?resource ualids:year_created '%s'^^xsd:string ; info:hasModel 'GenericFile'^^xsd:string ; dcterm:type 'Thesis'^^xsd:string" % (result['year_created']['value'])
            construct = self.construct
            for pair in self.mapping:
                construct = "%s ; <%s> ?%s" % (construct, pair[0], removeNS(pair[0]))
                where = " %s . OPTIONAL { ?resource <%s> ?%s }" % (where, pair[1], removeNS(pair[0]))
            self.queries.append( ( "%s %s } %s }" % (self.prefixes, construct, where), result['year_created']['value'] ))
        print(self.queries[0])


##  DATA TRANSPORT OBJECTS
##### Runs a query, sends data to get transformed, saves data to appropriate file

In [254]:
class Data(object):
    def __init__(self, q, sparqlData, sparqlTerms, ptype):
        self.q = q
        self.query = q[0]
        self.sparqlData = sparqlData
        self.sparqlTerms = sparqlTerms
        self.filename = ""
        self.output = []
        self.ptype = ptype

    def transformData(self):
        self.sparqlData.setMethod("GET")
        self.sparqlData.setReturnFormat(JSON)
        self.sparqlData.setQuery(self.query)
        results = self.sparqlData.query().convert()['results']['bindings']
        for result in results:
            try:
                result = TransformationFactory().getTransformation(result, self.ptype)
            except:
                PrintException()
            try:
                if isinstance(result, list):
                    for triple in result:
                        s = "<%s>" % (str(triple['subject']['value']))
                        p = "<%s>" % (str(triple['predicate']['value']))
                        if triple['object']['type'] == 'uri':
                            o = "<%s>" % (str(triple['object']['value']))
                        else:
                            o = "\"%s\"" % (str(triple['object']['value']))
                        self.output.append("%s %s %s . \n" % (s, p, o))
            except:
                PrintException()
        try:
            with open(self.filename, "w+") as f:
                f.writelines(self.output)
        except:
            PrintException()

        #with concurrent.futures.ThreadPoolExecutor(max_workers=6) as executor:
        #    future_to_result = {executor.submit(self.processResults, results, query): result for result in results}
        #    for future in concurrent.futures.as_completed(future_to_result):
        #        result = future_to_result[future]
        #        try:
        #            future.result()
        #        except Exception:
        #            PrintException()

class CollectionData(Data):
    def __init__(self, q, sparqlData, sparqlTerms, ptype):
        super().__init__(q, sparqlData, sparqlTerms, ptype)
        self.filename = 'results/collection.nt'

class CommunityData(Data):
    def __init__(self, q, sparqlData, sparqlTerms, ptype):
        super().__init__(q, sparqlData, sparqlTerms, ptype)
        self.filename = 'results/community.nt'


class ThesisData(Data):
    def __init__(self, q, sparqlData, sparqlTerms, ptype):
        super().__init__(q, sparqlData, sparqlTerms, ptype)
        self.filename = "results/thesis/%s.nt" % (self.q[1])


class GenericData(Data):
    def __init__(self, q, sparqlData, sparqlTerms, ptype):
        super().__init__(q, sparqlData, sparqlTerms, ptype)
        self.filename = "results/generic/%s.nt" % (self.q[1])

In [255]:
class QueryFactory():
	@staticmethod
	def getMigrationQuery(ptype):
		""" returns a specified query object depending on the type passed in"""
		if (ptype == "collection"):
			return Collection()
		elif (ptype == "community"):
			return Community()
		elif (ptype == "thesis"):
			return Thesis()
		elif (ptype == "generic"):
			return Generic()
		else:
			return None

In [256]:
class DataFactory():
	@staticmethod
	def getData(q, mig):
		""" returns a specified query object depending on the type passed in"""
		if (mig.ptype == "collection"):
			return CollectionData(q, mig.sparqlData, mig.sparqlTerms, mig.ptype)
		elif (mig.ptype == "community"):
			return CommunityData(q, mig.sparqlData, mig.sparqlTerms, mig.ptype)
		elif (mig.ptype == "thesis"):
			return ThesisData(q, mig.sparqlData, mig.sparqlTerms, mig.ptype)
		elif (mig.ptype == "generic"):
			return GenericData(q, mig.sparqlData, mig.sparqlTerms, mig.ptype)
		else:
			return None

In [257]:
class TransformationFactory():
    @staticmethod
    def getTransformation(triple, ptype):
        function = re.sub(r'[0-9]+', '', triple['predicate']['value'].split('/')[-1].replace('#', '').replace('-', ''))
        functions = {"rdfsyntaxnstype": Transformation().rdfsyntaxnstype(triple, ptype),
                     "language": Transformation().language(triple, ptype),
                     "type": Transformation().type(triple, ptype),
                     "rights": Transformation().rights(triple, ptype),
                     "license": Transformation().license(triple, ptype)
                    }
        if function in functions:
            functions[function]
        else:
            return [triple]

In [258]:
if __name__ == "__main__":
	main()

collection
collection
collection
collection
collection
collection
collection
collection
collection
collection
collection
collection
collection
collection
collection
community
community
community
community
community
community
community
community
community
community
community
community
community
community
community
community
community
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
g

generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic


generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic


generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic


generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic
generic


...

{'subject': {'value': 'http://gillingham.library.ualberta.ca:8080/fedora/rest/prod/b2/77/3x/95/b2773x95t', 'type': 'uri'}, 'predicate': {'value': 'http://purl.org/dc/terms/language', 'type': 'uri'}, 'object': {'value': 'English', 'datatype': 'http://www.w3.org/2001/XMLSchema#string', 'type': 'literal'}}
thesis
{'subject': {'value': 'http://gillingham.library.ualberta.ca:8080/fedora/rest/prod/b2/77/3x/95/b2773x95t', 'type': 'uri'}, 'predicate': {'value': 'http://purl.org/dc/terms/alternative', 'type': 'uri'}, 'object': {'value': 'L-Leucine uptake by Ammi visnaga', 'datatype': 'http://www.w3.org/2001/XMLSchema#string', 'type': 'literal'}}
thesis
{'subject': {'value': 'http://gillingham.library.ualberta.ca:8080/fedora/rest/prod/b2/77/3x/95/b2773x95t', 'type': 'uri'}, 'predicate': {'value': 'http://terms.library.ualberta.ca/unicorn', 'type': 'uri'}, 'object': {'value': '2678721', 'datatype': 'http://www.w3.org/2001/XMLSchema#string', 'type': 'literal'}}
thesis
{'subject': {'value': 'http:/

thesis
{'subject': {'value': 'http://gillingham.library.ualberta.ca:8080/fedora/rest/prod/t4/35/gf/90/t435gf90c', 'type': 'uri'}, 'predicate': {'value': 'http://terms.library.ualberta.ca/graduationDate', 'type': 'uri'}, 'object': {'value': '', 'datatype': 'http://www.w3.org/2001/XMLSchema#string', 'type': 'literal'}}
thesis
{'subject': {'value': 'http://gillingham.library.ualberta.ca:8080/fedora/rest/prod/t4/35/gf/90/t435gf90c', 'type': 'uri'}, 'predicate': {'value': 'http://terms.library.ualberta.ca/department', 'type': 'uri'}, 'object': {'value': 'Department of Recreation and Leisure Studies', 'datatype': 'http://www.w3.org/2001/XMLSchema#string', 'type': 'literal'}}
thesis
{'subject': {'value': 'http://gillingham.library.ualberta.ca:8080/fedora/rest/prod/t4/35/gf/90/t435gf90c', 'type': 'uri'}, 'predicate': {'value': 'http://terms.library.ualberta.ca/institution', 'type': 'uri'}, 'object': {'value': 'University of Alberta', 'datatype': 'http://www.w3.org/2001/XMLSchema#string', 'type

{'subject': {'value': 'http://gillingham.library.ualberta.ca:8080/fedora/rest/prod/pk/02/cd/46/pk02cd464', 'type': 'uri'}, 'predicate': {'value': 'http://purl.org/dc/terms/dateSubmitted', 'type': 'uri'}, 'object': {'value': '', 'datatype': 'http://www.w3.org/2001/XMLSchema#string', 'type': 'literal'}}
thesis
{'subject': {'value': 'http://gillingham.library.ualberta.ca:8080/fedora/rest/prod/pk/02/cd/46/pk02cd464', 'type': 'uri'}, 'predicate': {'value': 'http://purl.org/dc/terms/title', 'type': 'uri'}, 'object': {'value': 'The application of Tushman & Romanelli (1985), Miller (1990), Hinings and Greenwood (1988) and Pettigrew (1985) to retrospectively tracking strategic organizational change in a non-profit social service agency, 1975-1992', 'datatype': 'http://www.w3.org/2001/XMLSchema#string', 'type': 'literal'}}
thesis
{'subject': {'value': 'http://gillingham.library.ualberta.ca:8080/fedora/rest/prod/pk/02/cd/46/pk02cd464', 'type': 'uri'}, 'predicate': {'value': 'http://purl.org/dc/el

{'subject': {'value': 'http://gillingham.library.ualberta.ca:8080/fedora/rest/prod/b5/64/4t/56/b5644t56c', 'type': 'uri'}, 'predicate': {'value': 'http://terms.library.ualberta.ca/specialization', 'type': 'uri'}, 'object': {'value': '', 'datatype': 'http://www.w3.org/2001/XMLSchema#string', 'type': 'literal'}}
thesis
{'subject': {'value': 'http://gillingham.library.ualberta.ca:8080/fedora/rest/prod/b5/64/4t/56/b5644t56c', 'type': 'uri'}, 'predicate': {'value': 'http://purl.org/ontology/bibo/degree', 'type': 'uri'}, 'object': {'value': 'Master of Education in School and Counseling Psychology', 'datatype': 'http://www.w3.org/2001/XMLSchema#string', 'type': 'literal'}}
thesis
{'subject': {'value': 'http://gillingham.library.ualberta.ca:8080/fedora/rest/prod/b5/64/4t/56/b5644t56c', 'type': 'uri'}, 'predicate': {'value': 'http://purl.org/dc/terms/dateSubmitted', 'type': 'uri'}, 'object': {'value': '', 'datatype': 'http://www.w3.org/2001/XMLSchema#string', 'type': 'literal'}}
thesis
{'subjec

{'subject': {'value': 'http://gillingham.library.ualberta.ca:8080/fedora/rest/prod/pk/02/cc/66/pk02cc66d', 'type': 'uri'}, 'predicate': {'value': 'http://purl.org/dc/terms/dateSubmitted', 'type': 'uri'}, 'object': {'value': '', 'datatype': 'http://www.w3.org/2001/XMLSchema#string', 'type': 'literal'}}
thesis
{'subject': {'value': 'http://gillingham.library.ualberta.ca:8080/fedora/rest/prod/pk/02/cc/66/pk02cc66d', 'type': 'uri'}, 'predicate': {'value': 'http://purl.org/dc/terms/title', 'type': 'uri'}, 'object': {'value': 'Harijan education in India', 'datatype': 'http://www.w3.org/2001/XMLSchema#string', 'type': 'literal'}}
thesis
{'subject': {'value': 'http://gillingham.library.ualberta.ca:8080/fedora/rest/prod/pk/02/cc/66/pk02cc66d', 'type': 'uri'}, 'predicate': {'value': 'http://purl.org/dc/elements/1.1/subject', 'type': 'uri'}, 'object': {'value': 'Dalits--Education.', 'datatype': 'http://www.w3.org/2001/XMLSchema#string', 'type': 'literal'}}
thesis
{'subject': {'value': 'http://gil